In [22]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [23]:
!pip install requests_html

In [24]:
import csv
import sys
import requests
import math

In [25]:
headers = {
    'Content-Type': 'application/json',
    'Origin': 'https://ieeexplore.ieee.org',
}
pageNo = 1
recordIds = []
totalPages = pageNo
while(pageNo<=totalPages):
  data = '''{"action":"search",
  "newsearch":true,
  "matchBoolean":true,
  "queryText":"((\\"All Metadata\\":moon) AND \\"All Metadata\\":mars)",
  "ranges":["1872_2021_Year"],
  "highlight":true,
  "returnFacets":["ALL"],
  "returnType":"SEARCH",
  "matchPubs":true,
  "rowsPerPage":"100",
  "pageNumber":''' + str(pageNo) +'}'

  response = requests.post('https://ieeexplore.ieee.org/rest/search', headers=headers, data=str(data))
  # print(response)
  response = response.json()
  # print(response)
  # print(len(response['records']))
  splitInd = len('/document/')
  totalRecords = response['totalRecords']
  totalPages = math.ceil(totalRecords/100)
  recordsCount = min(totalRecords - (pageNo-1)*100, 100)
  records = response['records']
  print(totalPages, recordsCount)
  print(response)
  for recordInd in range(0, recordsCount):
    # print(records[0]['documentLink'][splitInd:-1])
    # print(recordInd)
    try:
      recordIds.append(records[recordInd]['documentLink'][splitInd:-1])
      # print(recordInd, records[recordInd]['documentLink'][splitInd:-1])
    except Exception as e:
      print(repr(e), 'Document link not available :', recordInd+(pageNo-1)*100+1)
  pageNo+=1
print(len(recordIds))

7 100
{'userInfo': {'institute': False, 'member': False, 'individual': False, 'guest': False, 'subscribedContent': False, 'fileCabinetContent': False, 'fileCabinetUser': False, 'institutionalFileCabinetUser': False, 'ip': '35.221.214.109', 'showPatentCitations': True, 'showGet802Link': False}, 'records': [{'authors': [{'preferredName': 'John A. Grant', 'normalizedName': 'J. A. Grant', 'firstName': 'John A.', 'lastName': 'Grant', 'searchablePreferredName': 'John A. Grant', 'id': 37707395500}, {'preferredName': 'Carlton J. Leuschen', 'normalizedName': 'C. J. Leuschen', 'firstName': 'Carlton J.', 'lastName': 'Leuschen', 'searchablePreferredName': 'Carlton J. Leuschen', 'id': 37284757000}], 'patentCitationCount': 0, 'accessType': {'type': 'locked', 'message': 'Full text access may be available. Click article title to sign in or learn about subscription options.'}, 'publicationNumber': '5941184', 'publicationYear': '2011', 'documentLink': '/document/5960711/', 'ephemera': False, 'articleNum

In [26]:
print(len(recordIds))

633


In [27]:
bibs = []
headers={
    'Accept': 'application/json',
    # 'Content-Type':'application/json'
}
data={
    'recordIds' : None,
    'download-format' : 'download-bibtex',
    'citations-format' :'citation-abstract'
}
url = 'https://ieeexplore.ieee.org/xpl/downloadCitations'
for recordId in recordIds:
  try:
    print(recordId)
    data['recordIds'] = str(recordId)
    response = requests.post(url, headers=headers, data=data) 
    bib = response.text
    # print(bib)
    bib = bib.replace("<br>", "")
    # print(bib)
    bibtex = bib.strip("}").strip("\t ") + '\n'
    # print(bibtex)
    ind = bibtex.index("{")
    bib_dict = {}
    bib_dict["type"] = bibtex[:ind]
    bibtex = bibtex[ind+1:]
    ind = bibtex.index("\n")
    bib_dict["id"] = bibtex[:ind-1]
    bibtex = bibtex[ind+1:]
    while(bibtex != "" and bibtex != "\n"): #len(bibtext) > 3):
      # print(bibtex)
      # print("bib", bibtex, len(bibtex))
      ind = bibtex.index("\n")
      attribute = bibtex[:ind].strip("\t,")
      # print("attr",attribute)
      try:
        ind_attr = attribute.index("=")
      except Exception as e:
        bibtex = bibtex[1:]
        continue
      # print(ind_attr)
      bib_dict[attribute[:ind_attr].strip()] = attribute[ind_attr+1:].strip('{} \r,')
      bibtex = bibtex[ind + 1:]
    # print(bib_dict)
    bibs.append(bib_dict)
  except Exception as e:
    continue

5960711
7549812
9127918
8002938
8741619
8212180
7500772
1659532
7943726
4161698
8955661
8741788
8742151
5286358
1607331
4839345
7500686
4463246
7231749
5293423
5446852
1559351
7500754
1367598
4977613
1559716
4526273
5747261
4161316
5747221
4977612
4148897
5325408
6497195
9024402
4839340
8136206
791544
5286356
794346
4659341
6318177
792447
7118956
7119273
9172532
8747312
4526265
7500766
1559312
6187064
8741598
1559460
6187004
4161385
8136702
5446737
8747314
171518
8077487
8467625
8396720
7935298
7943981
9172617
9213607
1655792
8396506
1518328
680071
7119287
6836181
8396416
1368103
8869589
9172540
6051217
798148
4977614
1559319
6187124
5747607
1589824
6361761
5168170
7943576
9103997
8810398
8440998
408086
660242
1559320
6497158
1652286
1655847
7118925
675849
4526513
5747267
941737
7119104
1559731
1656000
7500635
4526327
1559318
7943887
1656178
708444
1512573
8396422
7772495
1559417
7943566
7500869
7943895
716836
6187265
8396784
4839706
5286361
879842
1235059
6836251
8827273
1631789
49776

In [28]:
print(len(bibs), bibs)

633 [{'type': '@INPROCEEDINGS', 'id': '5960711,', 'author': 'J. A. {Grant} and C. J. {Leuschen', 'booktitle': '2011 IEEE RadarCon (RADAR)', 'title': 'The strata ground penetrating radar as a means for constraining the near surface properties of the Moon and Mars', 'year': '2011', 'volume': '', 'number': '', 'pages': '1132-1134', 'abstract': 'Strata is a low-mass, low-power, and low-volume impulse ground penetrating radar operating at 400 MHz and capable of defining subsurface stratigraphy and structure at the spatial resolution of tens of centimeters to 10-15 m depth. Strata would be used along transects suitable for to characterizing regolith properties on the Moon or distinguishing habitable environments on Mars.', 'keywords': 'astronomical instruments;ground penetrating radar;Mars;Moon;planetary surfaces;stratigraphy;strata ground penetrating radar;Moon;Mars;subsurface stratigraphy;astronomical instrument;frequency 400 MHz;Ground penetrating radar;Moon;Mars;Antennas;Geology;Instrume

In [29]:
output_json = {}
for bib in range(0, len(bibs)):
  print(bibs[bib])
  output_json[bib] = bibs[bib]

{'type': '@INPROCEEDINGS', 'id': '5960711,', 'author': 'J. A. {Grant} and C. J. {Leuschen', 'booktitle': '2011 IEEE RadarCon (RADAR)', 'title': 'The strata ground penetrating radar as a means for constraining the near surface properties of the Moon and Mars', 'year': '2011', 'volume': '', 'number': '', 'pages': '1132-1134', 'abstract': 'Strata is a low-mass, low-power, and low-volume impulse ground penetrating radar operating at 400 MHz and capable of defining subsurface stratigraphy and structure at the spatial resolution of tens of centimeters to 10-15 m depth. Strata would be used along transects suitable for to characterizing regolith properties on the Moon or distinguishing habitable environments on Mars.', 'keywords': 'astronomical instruments;ground penetrating radar;Mars;Moon;planetary surfaces;stratigraphy;strata ground penetrating radar;Moon;Mars;subsurface stratigraphy;astronomical instrument;frequency 400 MHz;Ground penetrating radar;Moon;Mars;Antennas;Geology;Instruments',

In [30]:
print(output_json)

{0: {'type': '@INPROCEEDINGS', 'id': '5960711,', 'author': 'J. A. {Grant} and C. J. {Leuschen', 'booktitle': '2011 IEEE RadarCon (RADAR)', 'title': 'The strata ground penetrating radar as a means for constraining the near surface properties of the Moon and Mars', 'year': '2011', 'volume': '', 'number': '', 'pages': '1132-1134', 'abstract': 'Strata is a low-mass, low-power, and low-volume impulse ground penetrating radar operating at 400 MHz and capable of defining subsurface stratigraphy and structure at the spatial resolution of tens of centimeters to 10-15 m depth. Strata would be used along transects suitable for to characterizing regolith properties on the Moon or distinguishing habitable environments on Mars.', 'keywords': 'astronomical instruments;ground penetrating radar;Mars;Moon;planetary surfaces;stratigraphy;strata ground penetrating radar;Moon;Mars;subsurface stratigraphy;astronomical instrument;frequency 400 MHz;Ground penetrating radar;Moon;Mars;Antennas;Geology;Instrumen

In [31]:
import json
filename = "/content/drive/My Drive/bibtex_ieee.json"    
with open(filename, 'w') as outfile:
    json.dump(output_json, outfile)